In [1]:
import numpy as np

import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json 

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim 

import requests 
from pandas.io.json import json_normalize 

import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

from bs4 import BeautifulSoup

import xml

!conda install -c conda-forge folium=0.5.0 --yes
import folium 

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


# Extracting 'List of US Cities by population' Wikipedia page into a text file

In [2]:
link = 'https://en.wikipedia.org/wiki/List_of_United_States_cities_by_population'
page = requests.get(link) 
soup = BeautifulSoup(page.text)

In [3]:
table = soup.find_all('table')[4]

In [4]:
table_rows = table.find_all('tr')
res = []
for tr in table_rows:
    td = tr.find_all('td')
    row = [tr.text.strip() for tr in td if tr.text.strip()]
    if row:
        res.append(row)
df = pd.DataFrame(res, columns=["Rank", "City", "State", "del1", "del2", "del3", "Sq.Area", "del5", "population density in Sq Mi", "Population density in Km2", "Location"])
df.head()

Rank         City       State       del1       del2     del3      Sq.Area  \
0    1  New York[d]    New York  8,398,748  8,175,133   +2.74%  301.5 sq mi   
1    2  Los Angeles  California  3,990,456  3,792,621   +5.22%  468.7 sq mi   
2    3      Chicago    Illinois  2,705,994  2,695,598   +0.39%  227.3 sq mi   
3    4   Houston[3]       Texas  2,325,502  2,100,263  +10.72%  637.5 sq mi   
4    5      Phoenix     Arizona  1,660,272  1,445,632  +14.85%  517.6 sq mi   

          del5 population density in Sq Mi Population density in Km2  \
0    780.9 km2                28,317/sq mi                10,933/km2   
1  1,213.9 km2                 8,484/sq mi                 3,276/km2   
2    588.7 km2                11,900/sq mi                 4,600/km2   
3  1,651.1 km2                 3,613/sq mi                 1,395/km2   
4  1,340.6 km2                 3,120/sq mi                 1,200/km2   

                                            Location  
0  40°39′49″N 73°56′19″W﻿ / ﻿40.6635°N 73.9387°W﻿...  
1  34°01′10″N 118°24′39″W﻿ / ﻿34.0194°N 118.4108°...  
2  41°50′15″N 87°40′54″W﻿ / ﻿41.8376°N 87.6818°W﻿...  
3  29°47′12″N 95°23′27″W﻿ / ﻿29.7866°N 95.3909°W﻿...  
4  33°34′20″N 112°05′24″W﻿ / ﻿33.5722°N 112.0901°...

In [5]:
new= df["Sq.Area"].str.split("s", n=1, expand = True)
new = new[0].str.replace(u'\xa0',u'')
df["Sq.Area"] = new.str.replace(',','')
df["Sq.Area"] = df["Sq.Area"].astype(float)
df["Radius"] = np.sqrt(df["Sq.Area"])

In [6]:
df.drop(columns = ["Rank", "del1", "del2", "del3", "del5", "Sq.Area", "population density in Sq Mi"], inplace = True)
df

City                 State Population density in Km2  \
0          New York[d]              New York                10,933/km2   
1          Los Angeles            California                 3,276/km2   
2              Chicago              Illinois                 4,600/km2   
3           Houston[3]                 Texas                 1,395/km2   
4              Phoenix               Arizona                 1,200/km2   
5      Philadelphia[e]          Pennsylvania                 4,511/km2   
6          San Antonio                 Texas                 1,250/km2   
7            San Diego            California                 1,670/km2   
8               Dallas                 Texas                 1,493/km2   
9             San Jose            California                 2,231/km2   
10              Austin                 Texas                 1,170/km2   
11     Jacksonville[f]               Florida                   455/km2   
12          Fort Worth                 Texas                   962/km2   
13            Columbus                  Ohio                 1,520/km2   
14    San Francisco[g]            California                 7,170/km2   
15           Charlotte        North Carolina                 1,064/km2   
16     Indianapolis[h]               Indiana                   914/km2   
17             Seattle            Washington                 3,245/km2   
18           Denver[i]              Colorado                 1,746/km2   
19       Washington[j]  District of Columbia                 4,304/km2   
20              Boston         Massachusetts                 5,381/km2   
21             El Paso                 Texas                 1,030/km2   
22             Detroit              Michigan                 1,871/km2   
23        Nashville[k]             Tennessee                   536/km2   
24            Portland                Oregon                 1,851/km2   
25             Memphis             Tennessee                   794/km2   
26       Oklahoma City              Oklahoma                   407/km2   
27           Las Vegas                Nevada                 1,818/km2   
28       Louisville[l]              Kentucky                   903/km2   
29        Baltimore[m]              Maryland                 2,934/km2   
30           Milwaukee             Wisconsin                 2,388/km2   
31         Albuquerque            New Mexico                 1,147/km2   
32              Tucson               Arizona                   888/km2   
33              Fresno            California                 1,762/km2   
34                Mesa               Arizona                 1,357/km2   
35          Sacramento            California                 1,953/km2   
36             Atlanta               Georgia                 1,366/km2   
37         Kansas City              Missouri                   590/km2   
38    Colorado Springs              Colorado                   918/km2   
39               Miami               Florida                 4,865/km2   
40             Raleigh        North Carolina                 1,221/km2   
41               Omaha              Nebraska                 1,296/km2   
42          Long Beach            California                 3,609/km2   
43   Virginia Beach[m]              Virginia                   710/km2   
44             Oakland            California                 2,901/km2   
45         Minneapolis             Minnesota                 2,960/km2   
46               Tulsa              Oklahoma                   791/km2   
47           Arlington                 Texas                 1,600/km2   
48               Tampa               Florida                 1,284/km2   
49      New Orleans[n]             Louisiana                   892/km2   
50             Wichita                Kansas                   939/km2   
51           Cleveland                  Ohio                 1,917/km2   
52         Bakersfield            California                   976/km2   
53              Aurora

In [7]:
df["Location"]= df["Location"].str.split("/", n = 2, expand = True)[1]
df.head()

City       State Population density in Km2  \
0  New York[d]    New York                10,933/km2   
1  Los Angeles  California                 3,276/km2   
2      Chicago    Illinois                 4,600/km2   
3   Houston[3]       Texas                 1,395/km2   
4      Phoenix     Arizona                 1,200/km2   

                   Location     Radius  
0    ﻿40.6635°N 73.9387°W﻿   17.363755  
1   ﻿34.0194°N 118.4108°W﻿   21.649480  
2    ﻿41.8376°N 87.6818°W﻿   15.076472  
3    ﻿29.7866°N 95.3909°W﻿   25.248762  
4   ﻿33.5722°N 112.0901°W﻿   22.750824

In [8]:
new = df["Location"].str.split(" ", n = 0, expand = False)
k = df.copy(deep = True)

In [9]:
Latitude = []
Longitude = []
for i in range(len(new)):
    Latitude.append(new[i][1][:-2])
    Longitude.append(new[i][2][:-3]) 

k["Latitude"] = Latitude
k["Longitude"] = Longitude
k["Latitude"] = k["Latitude"].str.replace(u'\ufeff',u'')
k.drop(columns = ["Location"], inplace = True)
k.head()
df = k.copy(deep = True)

In [10]:
df['Longitude'] = -df['Longitude'].astype(float)
df['Latitude'] = df['Latitude'].astype(float)
df['Radius'] = df['Radius']* 1000
df.head()

City       State Population density in Km2        Radius  Latitude  \
0  New York[d]    New York                10,933/km2  17363.755354   40.6635   
1  Los Angeles  California                 3,276/km2  21649.480363   34.0194   
2      Chicago    Illinois                 4,600/km2  15076.471736   41.8376   
3   Houston[3]       Texas                 1,395/km2  25248.762346   29.7866   
4      Phoenix     Arizona                 1,200/km2  22750.824161   33.5722   

   Longitude  
0   -73.9387  
1  -118.4108  
2   -87.6818  
3   -95.3909  
4  -112.0901

# Get US State Income per Capita

In [11]:
!pip install requests

In [12]:
website_url = requests.get('https://en.wikipedia.org/wiki/List_of_United_States_counties_by_per_capita_income').text
soup1 = BeautifulSoup(website_url,'lxml')
table = soup1.find('table',{'class':'wikitable sortable'})

In [13]:
table_rows = table.find_all('tr')
res = []
for tr in table_rows:
    td = tr.find_all('td')
    row = [tr.text.strip() for tr in td if tr.text.strip()]
    if row:
        res.append(row)
df_state = pd.DataFrame(res, columns=["Rank", "Country-equivalent", "State", "Per capita income", "del2", "del3", "Population", "del5"])
df_state.head()

Rank Country-equivalent       State Per capita income      del2      del3  \
0    1    New York County    New York           $62,498   $69,659   $84,627   
1    2          Arlington    Virginia           $62,018  $103,208  $139,244   
2    3  Falls Church City    Virginia           $59,088  $120,000  $152,857   
3    4              Marin  California           $56,791   $90,839  $117,357   
4    5    Alexandria City    Virginia           $54,608   $85,706  $107,511   

  Population     del5  
0  1,605,272  736,192  
1    214,861   94,454  
2     12,731    5,020  
3    254,643  102,912  
4    143,684   65,369

In [14]:
df_state.drop(columns = ['Rank','del2', 'del3', 'del5'], axis = 1, inplace = True)

In [15]:
df_state.head()

Country-equivalent       State Per capita income Population
0    New York County    New York           $62,498  1,605,272
1          Arlington    Virginia           $62,018    214,861
2  Falls Church City    Virginia           $59,088     12,731
3              Marin  California           $56,791    254,643
4    Alexandria City    Virginia           $54,608    143,684

## Plotting US cities extracted from Wiki page, using their coordinates

In [16]:
map_tohood = folium.Map(location=[37.0902,-95.7129], zoom_start=3)

In [17]:
map_tohood

In [18]:
!conda install -c conda-forge folium=0.5.0 --yes 
import folium 
import webbrowser

Solving environment: done

# All requested packages already installed.



In [19]:
for lat, lng, city, state in zip(df['Latitude'], df['Longitude'], df['City'], df['State']):
    label = '{}, {}'.format(city, state)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_tohood)
map_tohood

### Define FourSquare Credentials

In [20]:
CLIENT_ID = 'DNZIOZMR5T1IXJ3XHMK31GVGA2GPX0RFTSEPUKDY3VRTM0BZ'
CLIENT_SECRET = 'MDXU4NK3WBHR04NBG1RUPI5JJTDYHSCXUP02NUR05GV10D0V'
VERSION = '20180602'
LIMIT = 20
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: DNZIOZMR5T1IXJ3XHMK31GVGA2GPX0RFTSEPUKDY3VRTM0BZ
CLIENT_SECRET:MDXU4NK3WBHR04NBG1RUPI5JJTDYHSCXUP02NUR05GV10D0V


In [21]:
def getNearbyVenues(names, latitudes, longitudes, radius):
    
    venues_list=[]
    for name, lat, lng, radius in zip(names, latitudes, longitudes, radius):
        print(name)
        
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, radius, LIMIT)
        
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        venues_list.append([( name, lat, lng, v['venue']['name'], v['venue']['location']['lat'], v['venue']['location']['lng'], v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City', 'Latitude', 'Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude', 'Venue Category']
    
    return(nearby_venues)

In [22]:
df_venues = getNearbyVenues(names = df['City'], latitudes = df['Latitude'],longitudes = df['Longitude'], radius = df['Radius'])
df_venues.head()

New York[d]
Los Angeles
Chicago
Houston[3]
Phoenix
Philadelphia[e]
San Antonio
San Diego
Dallas
San Jose
Austin
Jacksonville[f]
Fort Worth
Columbus
San Francisco[g]
Charlotte
Indianapolis[h]
Seattle
Denver[i]
Washington[j]
Boston
El Paso
Detroit
Nashville[k]
Portland
Memphis
Oklahoma City
Las Vegas
Louisville[l]
Baltimore[m]
Milwaukee
Albuquerque
Tucson
Fresno
Mesa
Sacramento
Atlanta
Kansas City
Colorado Springs
Miami
Raleigh
Omaha
Long Beach
Virginia Beach[m]
Oakland
Minneapolis
Tulsa
Arlington
Tampa
New Orleans[n]
Wichita
Cleveland
Bakersfield
Aurora
Anaheim
Honolulu[b]
Santa Ana
Riverside
Corpus Christi
Lexington[o]
Stockton
Henderson
Saint Paul
St. Louis[m]
Cincinnati
Pittsburgh
Greensboro
Anchorage[p]
Plano
Lincoln
Orlando
Irvine
Newark
Toledo
Durham
Chula Vista
Fort Wayne
Jersey City
St. Petersburg
Laredo
Madison
Chandler
Buffalo
Lubbock
Scottsdale
Reno
Glendale
Gilbert[q]
Winston–Salem
North Las Vegas
Norfolk[m]
Chesapeake[m]
Garland
Irving
Hialeah
Fremont
Boise[r]
Richmond[m]
B

City  Latitude  Longitude                                     Venue  \
0  New York[d]   40.6635   -73.9387                                        Ix   
1  New York[d]   40.6635   -73.9387                   Brooklyn Botanic Garden   
2  New York[d]   40.6635   -73.9387                                Covenhoven   
3  New York[d]   40.6635   -73.9387  Prospect Park Boathouse & Audubon Center   
4  New York[d]   40.6635   -73.9387                           Brooklyn Museum   

   Venue Latitude  Venue Longitude    Venue Category  
0       40.660844       -73.961344              Café  
1       40.667622       -73.963191  Botanical Garden  
2       40.675143       -73.960203          Beer Bar  
3       40.660884       -73.964949          Building  
4       40.671521       -73.963677        Art Museum

In [23]:
df_venues = getNearbyVenues(names=df['City'], latitudes=df['Latitude'],longitudes=df['Longitude'],radius=df['Radius'])
df_venues.head(5)

New York[d]
Los Angeles
Chicago
Houston[3]
Phoenix
Philadelphia[e]
San Antonio
San Diego
Dallas
San Jose
Austin
Jacksonville[f]
Fort Worth
Columbus
San Francisco[g]
Charlotte
Indianapolis[h]
Seattle
Denver[i]
Washington[j]
Boston
El Paso
Detroit
Nashville[k]
Portland
Memphis
Oklahoma City
Las Vegas
Louisville[l]
Baltimore[m]
Milwaukee
Albuquerque
Tucson
Fresno
Mesa
Sacramento
Atlanta
Kansas City
Colorado Springs
Miami
Raleigh
Omaha
Long Beach
Virginia Beach[m]
Oakland
Minneapolis
Tulsa
Arlington
Tampa
New Orleans[n]
Wichita
Cleveland
Bakersfield
Aurora
Anaheim
Honolulu[b]
Santa Ana
Riverside
Corpus Christi
Lexington[o]
Stockton
Henderson
Saint Paul
St. Louis[m]
Cincinnati
Pittsburgh
Greensboro
Anchorage[p]
Plano
Lincoln
Orlando
Irvine
Newark
Toledo
Durham
Chula Vista
Fort Wayne
Jersey City
St. Petersburg
Laredo
Madison
Chandler
Buffalo
Lubbock
Scottsdale
Reno
Glendale
Gilbert[q]
Winston–Salem
North Las Vegas
Norfolk[m]
Chesapeake[m]
Garland
Irving
Hialeah
Fremont
Boise[r]
Richmond[m]
B

KeyError: 'groups'

In [24]:
print(df_venues.shape)
df_venues.head()

(6261, 7)


City  Latitude  Longitude                                     Venue  \
0  New York[d]   40.6635   -73.9387                                        Ix   
1  New York[d]   40.6635   -73.9387                   Brooklyn Botanic Garden   
2  New York[d]   40.6635   -73.9387                                Covenhoven   
3  New York[d]   40.6635   -73.9387  Prospect Park Boathouse & Audubon Center   
4  New York[d]   40.6635   -73.9387                           Brooklyn Museum   

   Venue Latitude  Venue Longitude    Venue Category  
0       40.660844       -73.961344              Café  
1       40.667622       -73.963191  Botanical Garden  
2       40.675143       -73.960203          Beer Bar  
3       40.660884       -73.964949          Building  
4       40.671521       -73.963677        Art Museum

In [25]:
df_venues.groupby('City').count()

Latitude  Longitude  Venue  Venue Latitude  \
City                                                            
Abilene                  20         20     20              20   
Akron                    20         20     20              20   
Albuquerque              20         20     20              20   
Alexandria[m]            20         20     20              20   
Allen                    20         20     20              20   
Allentown                20         20     20              20   
Amarillo                 20         20     20              20   
Anaheim                  20         20     20              20   
Anchorage[p]             20         20     20              20   
Ann Arbor                20         20     20              20   
Antioch                  20         20     20              20   
Arlington                20         20     20              20   
Arvada                   20         20     20              20   
Athens[z]                20         20     20              20   
Atlanta                  20         20     20              20   
Augusta[t]               20         20     20              20   
Aurora                   40         40     40              40   
Austin                   20         20     20              20   
Bakersfield              20         20     20              20   
Baltimore[m]             20         20     20              20   
Baton Rouge[s]           20         20     20              20   
Beaumont                 20         20     20              20   
Bellevue                 20         20     20              20   
Berkeley                 20         20     20              20   
Billings                 20         20     20              20   
Birmingham               20         20     20              20   
Boise[r]                 20         20     20              20   
Boston                   20         20     20              20   
Boulder                  20         20     20              20   
Bridgeport               20         20     20              20   
Broken Arrow             20         20     20              20   
Brownsville              20         20     20              20   
Buffalo                  20         20     20              20   
Burbank                  20         20     20              20   
Cambridge                20         20     20              20   
Cape Coral               20         20     20              20   
Carlsbad                 20         20     20              20   
Carrollton               20         20     20              20   
Cary[v]                  20         20     20              20   
Cedar Rapids             20         20     20              20   
Centennial               20         20     20              20   
Chandler                 20         20     20              20   
Charleston               20         20     20              20   
Charlotte                20         20     20              20   
Chattanooga              20         20     20              20   
Chesapeake[m]            20         20     20              20   
Chicago                  20         20     20              20   
Chula Vista              20         20     20              20   
Cincinnati               20         20     20              20   
Clarksville              20         20     20              20   
Clearwater               20         20     20              20   
Cleveland                20         20     20              20   
Clinton[ae]              20         20     20              20   
Clovis                   20         20     20              20   
College Station          20         20     20              20   
Colorado Springs         20         20     20              20   
Columbia                 40         40     40              40   
Columbus                 20         20     20              20   
Columbus[u]              20         20     20              20   
Concord                  20         20     20         

In [26]:
print('There are {} uniques categories.'.format(len(df_venues['Venue Category'].unique())))

There are 340 uniques categories.


In [27]:
c = pd.get_dummies(df_venues[['Venue Category']], prefix="", prefix_sep="")

c['City'] = df_venues['City'] 

fixed_columns = [c.columns[-1]] + list(c.columns[:-1])
c = c[fixed_columns]

c.head()

City  Accessories Store  African Restaurant  Airport  \
0  New York[d]                  0                   0        0   
1  New York[d]                  0                   0        0   
2  New York[d]                  0                   0        0   
3  New York[d]                  0                   0        0   
4  New York[d]                  0                   0        0   

   American Restaurant  Animal Shelter  Antique Shop  Aquarium  Arcade  \
0                    0               0             0         0       0   
1                    0               0             0         0       0   
2                    0               0             0         0       0   
3                    0               0             0         0       0   
4                    0               0             0         0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           1   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Dealership  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0                0          0           0       0     0    0               0   
1                0          0           0       0     0    0               0   
2                0          0           0       0     0    0               0   
3                0          0           0       0     0    0               0   
4                0          0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  Beach Bar  \
0                 0                 0                   0      0          0   
1                 0                 0                   0      0          0   
2                 0                 0                   0      0          0   
3                 0                 0                   0      0          0   
4                 0                 0                   0      0          0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                0         0            0           0              0   
1                0         0            0           0              0   
2                0         1            0           0              0   
3                0         0            0           0              0   
4                0         0            0           0              0   

   Bike Shop  Bistro  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0          0       0          0                 0         0              0   
1          0       0          0                 1         0              0   
2          0       0          0                 0         0              0   
3          0       0          0                 0         0              0   
4          0       0          0                 0         0              0   

   Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  Bridge  \
0           0                     0               0        0       0   
1           0                     0               0        0       0   
2           0                     0               0        0       0   
3           0                     0               0        0       0   
4           0                 

In [28]:
c.shape

(6261, 341)

In [29]:
c_grouped = c.groupby('City').mean().reset_index()
c_grouped

City  Accessories Store  African Restaurant  Airport  \
0              Abilene               0.00               0.000     0.00   
1                Akron               0.00               0.000     0.00   
2          Albuquerque               0.00               0.000     0.00   
3        Alexandria[m]               0.00               0.000     0.00   
4                Allen               0.00               0.000     0.00   
5            Allentown               0.00               0.000     0.00   
6             Amarillo               0.00               0.000     0.00   
7              Anaheim               0.00               0.000     0.00   
8         Anchorage[p]               0.00               0.000     0.00   
9            Ann Arbor               0.00               0.000     0.00   
10             Antioch               0.00               0.000     0.00   
11           Arlington               0.00               0.000     0.00   
12              Arvada               0.00               0.000     0.00   
13           Athens[z]               0.00               0.000     0.00   
14             Atlanta               0.00               0.000     0.00   
15          Augusta[t]               0.00               0.000     0.00   
16              Aurora               0.00               0.025     0.00   
17              Austin               0.00               0.000     0.00   
18         Bakersfield               0.00               0.000     0.00   
19        Baltimore[m]               0.00               0.000     0.00   
20      Baton Rouge[s]               0.00               0.000     0.00   
21            Beaumont               0.00               0.000     0.00   
22            Bellevue               0.00               0.000     0.00   
23            Berkeley               0.00               0.000     0.00   
24            Billings               0.00               0.000     0.00   
25          Birmingham               0.00               0.000     0.00   
26            Boise[r]               0.00               0.000     0.00   
27              Boston               0.00               0.000     0.00   
28             Boulder               0.00               0.000     0.00   
29          Bridgeport               0.00               0.000     0.00   
30        Broken Arrow               0.00               0.000     0.00   
31         Brownsville               0.00               0.000     0.00   
32             Buffalo               0.00               0.000     0.00   
33             Burbank               0.00               0.000     0.00   
34           Cambridge               0.00               0.000     0.00   
35          Cape Coral               0.00               0.000     0.00   
36            Carlsbad               0.00               0.000     0.00   
37          Carrollton               0.00               0.000     0.00   
38             Cary[v]               0.00               0.000     0.00   
39        Cedar Rapids               0.00               0.000     0.00   
40          Centennial               0.00               0.000     0.00   
41            Chandler               0.00               0.000     0.00   
42          Charleston               0.00               0.000     0.00   
43           Charlotte               0.00               0.000     0.00   
44         Chattanooga               0.00               0.000     0.00   
45       Chesapeake[m]               0.00               0.000     0.00   
46             Chicago               0.00               0.050     0.00   
47         Chula Vista               0.00               0.000     0.00   
48          Cincinnati               0.00               0.000     0.00   
49         Clarksville               0.00               0.000     0.00   
50          Clearwater               0.00               0.000     0.00   
51           Cleveland               0.00               0.000     0.00   
52         Clinton[ae]               0.00               0.000     0.00   
53              Clovis

In [30]:
num_top_venues = 5
for city in c_grouped['City']:
    print("----"+city+"----")
    temp = c_grouped[c_grouped['City'] == city].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Abilene----
                 venue  freq
0          Coffee Shop  0.15
1        Grocery Store  0.10
2  American Restaurant  0.10
3        Deli / Bodega  0.05
4         Food Service  0.05


----Akron----
                   venue  freq
0  Performing Arts Venue  0.10
1     Italian Restaurant  0.10
2              Speakeasy  0.05
3             Art Museum  0.05
4       Baseball Stadium  0.05


----Albuquerque----
                    venue  freq
0                 Brewery  0.25
1          Science Museum  0.10
2                   Beach  0.05
3           Historic Site  0.05
4  Furniture / Home Store  0.05


----Alexandria[m]----
                      venue  freq
0                 BBQ Joint  0.10
1  Mediterranean Restaurant  0.10
2        Italian Restaurant  0.05
3       Arts & Crafts Store  0.05
4                   Theater  0.05


----Allen----
                venue  freq
0      Ice Cream Shop  0.15
1                Café  0.10
2          Donut Shop  0.10
3  Italian Restaurant  0.05
4         

In [31]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    return row_categories_sorted.index.values[0:num_top_venues]

In [32]:
import numpy as np
num_top_venues = 10
indicators = ['st', 'nd', 'rd']

columns = ['City']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

c_venues_sorted = pd.DataFrame(columns=columns)
c_venues_sorted['City'] = c['City']

for ind in np.arange(c.shape[0]):
    c_venues_sorted.iloc[ind, 1:] = return_most_common_venues(c.iloc[ind, :], num_top_venues)

c_venues_sorted.shape

(6261, 11)

#### Assign weights to categories that stakeholders want to consider

In [33]:
k = df_venues.copy(deep = True)
weights_dict={'American Restaurant':3,'African Restaurant':3,'Asian Restaurant':4,'Vietnamese Restaurant':2.5,'Turkish Restaurant':3,'Vegetarian / Vegan Restaurant':3.5,'Food Court':4,'Thai Restaurant':4,'Tex-Mex Restaurant':4.5,'Sushi Restaurant':4,'Italian Restaurant':4,'Steakhouse':4,'Spanish Restaurant':4,'Restaurant':5,'Latin American Restaurant':3}
data = df_venues['Venue Category']
allVenues = data.astype(object)

In [34]:
weights = []
for i in allVenues:
    if i in weights_dict.keys():
        weights.append(weights_dict[i])
    else :
        weights.append(0)
df_venues['weights'] = weights;
df_venues.head()

City  Latitude  Longitude                                     Venue  \
0  New York[d]   40.6635   -73.9387                                        Ix   
1  New York[d]   40.6635   -73.9387                   Brooklyn Botanic Garden   
2  New York[d]   40.6635   -73.9387                                Covenhoven   
3  New York[d]   40.6635   -73.9387  Prospect Park Boathouse & Audubon Center   
4  New York[d]   40.6635   -73.9387                           Brooklyn Museum   

   Venue Latitude  Venue Longitude    Venue Category  weights  
0       40.660844       -73.961344              Café      0.0  
1       40.667622       -73.963191  Botanical Garden      0.0  
2       40.675143       -73.960203          Beer Bar      0.0  
3       40.660884       -73.964949          Building      0.0  
4       40.671521       -73.963677        Art Museum      0.0

In [35]:
df_venues.drop(df_venues[df_venues.weights < 1.0].index, inplace=True)
df_venues.head()

City  Latitude  Longitude                          Venue  \
45     Chicago   41.8376   -87.6818  La Catedral Cafe & Restaurant   
50     Chicago   41.8376   -87.6818                      Ca Phe Da   
59     Chicago   41.8376   -87.6818       Yassa African Restaurant   
65  Houston[3]   29.7866   -95.3909       Coltivare Pizza & Garden   
86     Phoenix   33.5722  -112.0901                 Veggie Village   

    Venue Latitude  Venue Longitude                 Venue Category  weights  
45       41.846218       -87.708894                     Restaurant      5.0  
50       41.858012       -87.653601          Vietnamese Restaurant      2.5  
59       41.830780       -87.616906             African Restaurant      3.0  
65       29.781629       -95.393936             Italian Restaurant      4.0  
86       33.552807      -112.054706  Vegetarian / Vegan Restaurant      3.5

In [36]:
citywise_venues_weights = df_venues[['City','weights']].copy()
citywise_venues_weights_means = citywise_venues_weights.groupby(['City']).mean()
citywise_venues_weights_means = citywise_venues_weights_means.reset_index(drop=False)
citywise_venues_weights_means.head()

City  weights
0        Abilene      3.0
1          Akron      4.0
2    Albuquerque      3.0
3  Alexandria[m]      3.5
4          Allen      4.0

In [37]:
city_selection = pd.merge(df, citywise_venues_weights_means, on='City')
city_selection = city_selection[['City','Population density in Km2','weights']].copy()
city_selection.head()

City Population density in Km2   weights
0          Chicago                 4,600/km2  3.500000
1       Houston[3]                 1,395/km2  4.000000
2          Phoenix                 1,200/km2  3.833333
3  Philadelphia[e]                 4,511/km2  4.000000
4      San Antonio                 1,250/km2  4.000000

In [38]:
k = city_selection.copy(deep = True)
k['Population density in Km2'] = k['Population density in Km2'].str.split("/", n = 0, expand = True)
k['Population density in Km2'] = k['Population density in Km2'].str.replace(',','')
k['Population density in Km2'] = k['Population density in Km2'].astype(float)
city_selection = k.copy(deep = True)
city_selection.head()

City  Population density in Km2   weights
0          Chicago                     4600.0  3.500000
1       Houston[3]                     1395.0  4.000000
2          Phoenix                     1200.0  3.833333
3  Philadelphia[e]                     4511.0  4.000000
4      San Antonio                     1250.0  4.000000

### Normalize the Data frame

In [39]:
from sklearn import preprocessing
column_names_to_normalize = ['Population density in Km2', 'weights']
x = city_selection[column_names_to_normalize].values
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(x)
city_selection[column_names_to_normalize] = pd.DataFrame(x_scaled)
city_selection.head()

City  Population density in Km2   weights
0          Chicago                   0.664224  0.400000
1       Houston[3]                   0.194489  0.600000
2          Phoenix                   0.165909  0.533333
3  Philadelphia[e]                   0.651180  0.600000
4      San Antonio                   0.173238  0.600000

### Calculate the normalized column sums to determine the city with the highest sum to find the best fit

In [40]:
city_selection['sum'] = city_selection['Population density in Km2'] + city_selection['weights']
row_num = city_selection['sum'].argmax()
city_name = city_selection['City'].iloc[row_num]
city_name

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:2: FutureWarning: 
The current behaviour of 'Series.argmax' is deprecated, use 'idxmax'
instead.
The behavior of 'argmax' will be corrected to return the positional
maximum in the future. For now, use 'series.values.argmax' or
'np.argmax(np.array(values))' to get the position of the maximum
row.
  from ipykernel import kernelapp as app


'Daly City'

In [41]:
row = df.loc[df['City']== city_name].index[0]
state_name = df['State'].iloc[row]
state_name

'California'

### We will check to see if the Income per capita is high enough

In [42]:
p_row = df_state.loc[df_state['State'] == state_name].index[0]
per_capital_income = df_state['Per capita income'].iloc[p_row]
print("Per capita income of California is :", per_capital_income)

Per capita income of California is : $56,791


### We will now check which location in Paterson would be the best

In [43]:
lat_california = df['Latitude'].iloc[row]
long_california = df['Longitude'].iloc[row]
print(lat_california, long_california)

37.7009 -122.465


#### We will get all the venues in California using FourSquare API within our radius


In [44]:
def getNearbyVenues1(name, latitudes, longitudes, radius):
    
    LIMIT = 150       
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            latitudes, 
            longitudes, 
            radius, 
            LIMIT)
            
    results = requests.get(url).json()["response"]['groups'][0]['items']
    venues_list=[]
    venues_list.append([(name,lat,lng,v['venue']['name'],v['venue']['location']['lat'],v['venue']['location']['lng'],v['venue']['categories'][0]['name'])for v in results])
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City', 'Latitude', 'Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude','Venue Category']
    return(nearby_venues)


california_venues = getNearbyVenues1(name = 'Daly City', latitudes = lat_california ,longitudes = long_california, radius = 2500)
california_venues.head()

City  Latitude  Longitude                    Venue  Venue Latitude  \
0  Daly City   38.3539  -121.9728         Pet Food Express       37.697000   
1  Daly City   38.3539  -121.9728      Cold Stone Creamery       37.702159   
2  Daly City   38.3539  -121.9728             Bart Grocery       37.705672   
3  Daly City   38.3539  -121.9728      Red Ribbon Bakeshop       37.697230   
4  Daly City   38.3539  -121.9728  Scott Hyver Vision Care       37.698062   

   Venue Longitude     Venue Category  
0      -122.463299          Pet Store  
1      -122.470603     Ice Cream Shop  
2      -122.464151  Korean Restaurant  
3      -122.462932             Bakery  
4      -122.470748       Optical Shop

In [45]:
venues_in_california = california_venues.copy(deep = True)
venues_in_california.shape

(61, 7)

## Since there are 61 categories, we will weighs each category to improve results

In [60]:
venues_in_california.head

<bound method NDFrame.head of          City  Latitude  Longitude  \
0   Daly City   38.3539  -121.9728   
1   Daly City   38.3539  -121.9728   
2   Daly City   38.3539  -121.9728   
3   Daly City   38.3539  -121.9728   
4   Daly City   38.3539  -121.9728   
5   Daly City   38.3539  -121.9728   
6   Daly City   38.3539  -121.9728   
7   Daly City   38.3539  -121.9728   
8   Daly City   38.3539  -121.9728   
9   Daly City   38.3539  -121.9728   
10  Daly City   38.3539  -121.9728   
11  Daly City   38.3539  -121.9728   
12  Daly City   38.3539  -121.9728   
13  Daly City   38.3539  -121.9728   
14  Daly City   38.3539  -121.9728   
15  Daly City   38.3539  -121.9728   
16  Daly City   38.3539  -121.9728   
17  Daly City   38.3539  -121.9728   
18  Daly City   38.3539  -121.9728   
19  Daly City   38.3539  -121.9728   
20  Daly City   38.3539  -121.9728   
21  Daly City   38.3539  -121.9728   
22  Daly City   38.3539  -121.9728   
23  Daly City   38.3539  -121.9728   
24  Daly City   38.3

In [78]:
k = california_venues.copy(deep = True)
new_weightage_dict= {'Pet Store':1,
                    'Ice Cream Shop':3,
                    'Korean Restaurant':4,
                     'Bakery':3.5,
                     'Optical Shop':1,
                     'Filipino Restaurant':4,
                     'Deli / Bodega':3.5,
                     'Supermarket':2,
                     'Filipino Restaurant':4,
                     'Restaurant':5,
                     'Hawaiian Restaurant':4,
                     'Mexican Restaurant': 4,
                     'Golf Course':2,
                     'Shipping Store':1,
                     'Coffee Shop':3,
                     'Thrift / Vintage Store':2,
                     'Fast Food Restaurant':4,
                     'Bakery': 3.5,
                     'Athletics & Sports': 1,
                     'Sushi Restaurant': 4,
                     'Movie Theater': 3,
                     'Sandwich Place': 3.5,
                     'Grocery Store': 3,
                     'Gym / Fitness Center': 2,
                     'Lounge': 3,
                     'Filipino Restaurant': 4,
                     'Pizza Place': 3.5,
                     'Nature Preserve': 2,
                     'Diner':3.5,
                     'Discount Store': 1,
                     'Hookah Bar': 2.5,
                     'Italian Restaurant':4,
                     'Gym / Fitness Center': 2,
                     'Thai Restaurant': 4,
                     'Athletics & Sports': 1,
                     'Donut Shop': 3,
                     'Café': 3.5,
                     'Southern / Soul Food Restaurant': 4,
                     'Burger Joint': 3.5,
                     'Bakery': 3,
                     'Indian Restaurant': 4,
                     'Trail': 1,
                     'Spa': 2,
                     'Department Store': 2,
                     'Monument / Landmark': 2,
                     'Kebab Restaurant': 4,
                     'Pharmacy': 1,
                     'Asian Restaurant': 4,
                     'Park': 2,
                     'Pizza Place': 3.5,
                     'Park': 2,
                     'Church': 1,
                     'Playground': 2,
                     'Ice Cream Shop': 3,
                     'Playground': 2,
                     'Elementary School': 1,
                     'Flower Shop': 2,
                     'History Museum': 1,
                     'Trail': 1,
                     'Furniture / Home Store': 2,
                     'Trail': 1}
                     

### Plotting all the venues that we have got from the Four Square API

In [79]:
import matplotlib.cm as cm
import matplotlib.colors as colors
import folium

venues_map = folium.Map(location=[lat_california, long_california], zoom_start=15)


folium.features.CircleMarker(
    [lat_california, long_california],
    radius=10,
    popup='Daly City',
    fill=True,
    color='red',
    fill_color='red',
    fill_opacity=0.6
    ).add_to(venues_map)

In [71]:
for lat, lng, label in zip(venues_in_california['Venue Latitude'], venues_in_california['Venue Longitude'], venues_in_california['Venue']):
    label=folium.Popup(label,parse_html=True)
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.6,
        parse_html = False).add_to(venues_map)
venues_map

In [72]:
allVenuesinCity1 = k['Venue Category']

f_weights1 = []
for i in allVenuesinCity1:
    if i in new_weightage_dict.keys():
        f_weights1.append(new_weightage_dict[i])
    else :
        f_weights1.append(0)
k['weights'] = f_weights1;
k.head()

City  Latitude  Longitude                    Venue  Venue Latitude  \
0  Daly City   38.3539  -121.9728         Pet Food Express       37.697000   
1  Daly City   38.3539  -121.9728      Cold Stone Creamery       37.702159   
2  Daly City   38.3539  -121.9728             Bart Grocery       37.705672   
3  Daly City   38.3539  -121.9728      Red Ribbon Bakeshop       37.697230   
4  Daly City   38.3539  -121.9728  Scott Hyver Vision Care       37.698062   

   Venue Longitude     Venue Category  weights  
0      -122.463299          Pet Store      1.0  
1      -122.470603     Ice Cream Shop      3.0  
2      -122.464151  Korean Restaurant      4.0  
3      -122.462932             Bakery      3.0  
4      -122.470748       Optical Shop      1.0

In [73]:
newframe = k[['City','Venue Category','weights']].copy()
newframe = k.groupby(['Venue Category']).mean()
newframe.drop(columns = ["Latitude", "Longitude"], inplace = True)
newframe

Venue Latitude  Venue Longitude  weights
Venue Category                                                           
Asian Restaurant                      37.699835      -122.484027      4.0
Athletics & Sports                    37.688096      -122.469612      2.0
Bakery                                37.700980      -122.468335      3.0
Burger Joint                          37.717599      -122.473916      3.5
Café                                  37.707900      -122.454807      3.5
Church                                37.714081      -122.483060      1.0
Coffee Shop                           37.697357      -122.462970      3.0
Deli / Bodega                         37.694543      -122.471401      3.5
Department Store                      37.697662      -122.482424      2.0
Diner                                 37.703956      -122.475395      3.5
Discount Store                        37.706397      -122.460073      1.0
Donut Shop                            37.688784      -122.471605      3.0
Elementary School                     37.705739      -122.444238      1.0
Fast Food Restaurant                  37.688125      -122.472093      4.0
Filipino Restaurant                   37.695286      -122.465134      4.0
Flower Shop                           37.682962      -122.456958      2.0
Furniture / Home Store                37.685505      -122.446138      2.0
Golf Course                           37.696260      -122.472264      2.0
Grocery Store                         37.700376      -122.482614      3.0
Gym / Fitness Center                  37.699705      -122.468561      2.0
Hawaiian Restaurant                   37.697113      -122.463000      4.0
History Museum                        37.682090      -122.456184      1.0
Hookah Bar                            37.690051      -122.465513      2.5
Ice Cream Shop                        37.701353      -122.477078      3.0
Indian Restaurant                     37.700813      -122.483585      4.0
Italian Restaurant                    37.701560      -122.485494      4.0
Kebab Restaurant                      37.685801      -122.459826      4.0
Korean Restaurant                     37.705672      -122.464151      4.0
Lounge                                37.706864      -122.458855      3.0
Mexican Restaurant                    37.703373      -122.462920      4.0
Monument / Landmark                   37.707671      -122.483804      2.0
Movie Theater                         37.702153      -122.470737      3.0
Nature Preserve                       37.701258      -122.456404      2.0
Optical Shop                          37.698062      -122.470748      1.0
Park                                  37.715764      -122.458588      2.0
Pet Store                             37.697000      -122.463299      1.0
Pharmacy                              37.685571      -122.472689      1.0
Pizza Place                           37.693243      -122.476092      3.5
Playground                            37.710986      -122.450841      2.0
Restaurant                            37.701287      -122.470603      5.0
Sandwich Place                        37.693132      -122.474709      3.5
Shipping Store                        37.700388      -122.463980      1.0
Southern / Soul Food Restaurant       37.686896      -122.469615      4.0
Spa                                   37.699511      -122.483692      2.5
Supermarket                           37.694463      -122.471643      2.0
Sushi Restaurant                      37.702065      -122.470669      4.0
Thai Restaurant                       37.697113      -122.484236      4.0
Thrift / Vintage Store                37.705075      -122.462970      2.0
Trail                                 37.702236      -122.454450      1.0

## Using K Means algorithm to cluster the venues and calculating the weights for each cluster to decide which cluster would be the best area to put a restaurant

In [74]:
from scipy import stats
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt
import seaborn as sns

clmns = ['weights','Venue Latitude', 'Venue Longitude']
df_tr_std = stats.zscore(newframe[clmns])

kmeans = KMeans(n_clusters=3, random_state=0).fit(df_tr_std)
labels = kmeans.labels_
newframe['clusters'] = labels

clmns.extend(['clusters'])

kframe = newframe[clmns].groupby(['Venue Category']).mean()
kframe = kframe.reset_index(drop = False)
kframe.head()

Venue Category  weights  Venue Latitude  Venue Longitude  clusters
0    Asian Restaurant      4.0       37.699835      -122.484027         0
1  Athletics & Sports      2.0       37.688096      -122.469612         1
2              Bakery      3.0       37.700980      -122.468335         0
3        Burger Joint      3.5       37.717599      -122.473916         0
4                Café      3.5       37.707900      -122.454807         2

In [75]:
finalWeight = kframe.groupby(['clusters']).mean()
finalWeight

weights  Venue Latitude  Venue Longitude
clusters                                           
0         3.500000       37.700741      -122.475183
1         2.500000       37.688612      -122.465162
2         1.678571       37.705104      -122.460777

In [76]:
lat1 = 37.700741
long1 = -122.475183

#### We now have the location with the maximum weight, so we will plot it in the graph with a 50 meter radius for the new restaurant

In [77]:
final_map = folium.Map(location=[lat1, long1], zoom_start=15) 

folium.features.CircleMarker(
    [lat1, long1],
    radius=50,
    popup='Restaurant can be built within this circle',
    fill=True,
    color='green',
    fill_color='green',
    fill_opacity=0.6
    ).add_to(final_map)
final_map